In [1]:
import h5py,glob,os
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
from pycbc.inference import io, models
from pycbc.workflow import WorkflowConfigParser
from pycbc import conversions
# PLOTTING OPTIONS
fig_width_pt = 3*246.0  # Get this from LaTeX using \showthe\columnwidth
inches_per_pt = 1.0/72.27               # Convert pt to inch
golden_mean = (np.sqrt(5)-1.0)/2.0         # Aesthetic ratio
fig_width = fig_width_pt*inches_per_pt  # width in inches
fig_height = fig_width*golden_mean      # height in inches
fig_size =  [fig_width,fig_height]

params = { 'axes.labelsize': 24,
          'font.family': 'serif',
          'font.serif': 'Computer Modern Raman',
          'font.size': 24,
          'legend.fontsize': 20,
          'xtick.labelsize': 24,
          'ytick.labelsize': 24,
          'axes.grid' : True,
          'text.usetex': True,
          'savefig.dpi' : 100,
          'lines.markersize' : 14,
          'figure.figsize': fig_size}

mpl.rcParams.update(params)

In [2]:
import json
f = open('snrs.json')
 
# returns JSON object as
# a dictionary
snrs = json.load(f)

# Compute the Bayesian Evidence between 220 and 220_221

In [3]:
snr4 = {}
for name in snrs:
    if snrs[name]>4:
        snr4[name] = snrs[name]

In [8]:
results_220 = {}
results_221 = {}
for name in snr4:
    results_220[name] = glob.glob('./t10-4ogc-run/220/4ogcringdown_output/posterior_files/*'+name+'*.hdf')
    results_221[name] = glob.glob('./t10-4ogc-run/t2_220_221/4ogcringdown_output/posterior_files/*'+name+'*.hdf')

In [9]:
results_221

{'GW150914_095045': ['./t10-4ogc-run/t2_220_221/4ogcringdown_output/posterior_files/H1L1V1-EXTRACT_POSTERIOR_GW150914_095045-1126259200-400.hdf'],
 'GW170104_101158': ['./t10-4ogc-run/t2_220_221/4ogcringdown_output/posterior_files/H1L1V1-EXTRACT_POSTERIOR_GW170104_101158-1126259200-400.hdf'],
 'GW170121_212536': ['./t10-4ogc-run/t2_220_221/4ogcringdown_output/posterior_files/H1L1V1-EXTRACT_POSTERIOR_GW170121_212536-1126259200-400.hdf'],
 'GW170403_230611': ['./t10-4ogc-run/t2_220_221/4ogcringdown_output/posterior_files/H1L1V1-EXTRACT_POSTERIOR_GW170403_230611-1126259200-400.hdf'],
 'GW170727_010430': ['./t10-4ogc-run/t2_220_221/4ogcringdown_output/posterior_files/H1L1V1-EXTRACT_POSTERIOR_GW170727_010430-1126259200-400.hdf'],
 'GW170729_185629': ['./t10-4ogc-run/t2_220_221/4ogcringdown_output/posterior_files/H1L1V1-EXTRACT_POSTERIOR_GW170729_185629-1126259200-400.hdf'],
 'GW170809_082821': ['./t10-4ogc-run/t2_220_221/4ogcringdown_output/posterior_files/H1L1V1-EXTRACT_POSTERIOR_GW170809_

In [10]:
# load log_evidences
log_evidence_220 = {}
log_evidence_221 = {}
bayes_factors = {}

for name in results_220:
    if len(results_220[name])==1 and len(results_221[name])==1:
        res220 = h5py.File(results_220[name][0], 'r')
        res221 = h5py.File(results_221[name][0], 'r')

        log_evidence_220[name] = res220.attrs['log_evidence']
        log_evidence_221[name] = res221.attrs['log_evidence']

        res220.close()
        res221.close()
        
 # calculate log Bayes factors
for event in log_evidence_220:
    bayes_factors[event] = log_evidence_221[event] - log_evidence_220[event]

In [11]:
bayes_factors

{'GW150914_095045': 1.0982119096443057,
 'GW170104_101158': -0.005303401267156005,
 'GW170121_212536': -0.455439031124115,
 'GW170403_230611': 0.25637808052124456,
 'GW170727_010430': 0.3301863446831703,
 'GW170729_185629': -0.6547322552651167,
 'GW170809_082821': -0.6494601402664557,
 'GW170818_022509': -0.9791805656277575,
 'GW170823_131358': -0.6981566856411519,
 'GW190408_181802': -0.49354014825075865,
 'GW190412_053044': 0.006911098258569837,
 'GW190413_052954': -0.3801808216958307,
 'GW190413_134308': -0.7229392700828612,
 'GW190421_213856': 0.20982043305411935,
 'GW190424_180648': 0.17239702865481377,
 'GW190503_185404': -0.7888330044224858,
 'GW190512_180714': -0.21156122186221182,
 'GW190513_205428': -0.43760166596621275,
 'GW190514_065416': -0.5855263381963596,
 'GW190517_055101': 0.3641466610133648,
 'GW190519_153544': 1.622759877354838,
 'GW190521_030229': 0.6863308954052627,
 'GW190521_074359': 3.4836515481583774,
 'GW190602_175927': 0.9292952385148965,
 'GW190620_030421':

In [12]:
len(bayes_factors)

47

In [4]:
def get_snr(gwname,rundir = './t6-rerun4ogc-geocent_time/220_221/o3bringdown_output/'):
    snr = {}
    for name in gwname:
        configdir = glob.glob(rundir+'config_files/*'+name+'*')
        sampledir = glob.glob(rundir+'samples_files/*'+name+'*')
        cp = WorkflowConfigParser(configdir)
        fp = io.loadfile(sampledir[0], 'r')
        data = fp.read_data()                                                           
        psds = fp.read_psds()  
        samples = fp.read_samples(fp['samples'].keys())
        idx = samples['loglikelihood'].argmax()
        maxl_params = {p: samples[p][idx] for p in samples.fieldnames}
        model = models.read_from_config(cp,data=data,psds=psds)
        model.update(**maxl_params)
        snr[name] = conversions.snr_from_loglr(model.loglr)
    return snr

def get_loglr(gwname,rundir = './t6-rerun4ogc-geocent_time/220_221/o3bringdown_output/'):
    loglr = {}
    for name in gwname:
        configdir = glob.glob(rundir+'config_files/*'+name+'*')
        sampledir = glob.glob(rundir+'samples_files/*'+name+'*')
        cp = WorkflowConfigParser(configdir)
        fp = io.loadfile(sampledir[0], 'r')
        data = fp.read_data()                                                           
        psds = fp.read_psds()  
        samples = fp.read_samples(fp['samples'].keys())
        idx = samples['loglikelihood'].argmax()
        maxl_params = {p: samples[p][idx] for p in samples.fieldnames}
        model = models.read_from_config(cp,data=data,psds=psds)
        model.update(**maxl_params)
        loglr[name] = model.loglr
    return loglr

In [5]:
snr = get_snr(gwname)
loglr = get_loglr(gwname)

In [8]:
snr

{'GW191103_012549': 1.998092815319896,
 'GW191105_143521': 1.9103628446771173,
 'GW191109_010717': 11.858631535785431,
 'GW191113_071753': 2.7888549240463343,
 'GW191126_115259': 3.213505241485403,
 'GW191127_050227': 6.679740086844839,
 'GW191129_134029': 1.9988550054837504,
 'GW191204_110529': 2.856982445883923,
 'GW191204_171526': 2.2606490992975714,
 'GW191215_223052': 5.669957042062531,
 'GW191216_213338': 3.2321488906947216,
 'GW191219_163120': 3.2785737178636647,
 'GW191222_033537': 6.140627181484112,
 'GW191230_180458': 5.964284469909562,
 'GW200112_155838': 7.64042919006213,
 'GW200115_042309': 2.077339085598429,
 'GW200128_022011': 4.639083413113765,
 'GW200129_065458': 13.158240062292455,
 'GW200202_154313': 1.6704929613398565,
 'GW200208_130117': 5.408393348855938,
 'GW200208_222617': 4.523706174163526,
 'GW200209_085452': 4.365793950636084,
 'GW200210_092254': 2.8286837826137368,
 'GW200216_220804': 2.6281618540422866,
 'GW200219_094415': 6.336127908402623,
 'GW200220_0619

In [9]:
loglr

{'GW191103_012549': 1.9962145910831168,
 'GW191105_143521': 1.8714487277902663,
 'GW191109_010717': 70.3135707062902,
 'GW191113_071753': 3.8608028026646934,
 'GW191126_115259': 5.163308472489007,
 'GW191127_050227': 22.309431850910187,
 'GW191129_134029': 1.7290507298021112,
 'GW191204_110529': 4.081174348044442,
 'GW191204_171526': 2.5552658506203443,
 'GW191215_223052': 16.074205479351804,
 'GW191216_213338': 5.223396408298868,
 'GW191219_163120': 5.374519789591432,
 'GW191222_033537': 18.85365163348615,
 'GW191230_180458': 17.786350398673676,
 'GW200112_155838': 29.188079627230763,
 'GW200115_042309': 2.3534134465735406,
 'GW200128_022011': 10.76054910995299,
 'GW200129_065458': 86.56965112371836,
 'GW200202_154313': 1.2171216072165407,
 'GW200208_130117': 14.62536071287468,
 'GW200208_222617': 10.23199034348363,
 'GW200209_085452': 9.53007517522201,
 'GW200210_092254': 4.000725175545085,
 'GW200216_220804': 3.45361924401368,
 'GW200219_094415': 20.073314496548846,
 'GW200220_06192

# Bayes evidence

In [9]:
 # list samples files
results_dir_220 = "/work/julian.westerweck/projects/ringdown/4ogc/workflows/220_merger/4ogc/4ogc_ringdown_test_output/samples_files/"
results_dir_221 = "/work/yifan.wang/ringdown/t6-rerun4ogc-geocent_time/220_221/o3bringdown_output/samples_files/"

results_files_220 = os.listdir(results_dir_220)
results_files_221 = os.listdir(results_dir_221)

In [10]:
results_files_221

['H1L1V1-INFERENCE_GW191222_033537-1126259200-400.hdf',
 'H1L1V1-INFERENCE_GW200224_222234-1126259200-400.hdf',
 'H1L1V1-INFERENCE_GW200308_173609-1126259200-400.hdf',
 'H1L1V1-INFERENCE_GW200202_154313-1126259200-400.hdf',
 'H1L1V1-INFERENCE_GW200316_215756-1126259200-400.hdf',
 'H1L1V1-INFERENCE_GW191126_115259-1126259200-400.hdf',
 'H1L1V1-INFERENCE_GW200311_115853-1126259200-400.hdf',
 'H1L1V1-INFERENCE_GW200322_091133-1126259200-400.hdf',
 'H1L1V1-INFERENCE_GW191215_223052-1126259200-400.hdf',
 'H1L1V1-INFERENCE_GW191103_012549-1126259200-400.hdf',
 'plot_all_file.sh',
 'H1L1V1-INFERENCE_GW200112_155838-1126259200-400.hdf',
 'H1L1V1-INFERENCE_GW200208_130117-1126259200-400.hdf',
 'H1L1V1-INFERENCE_GW200219_094415-1126259200-400.hdf',
 'H1L1V1-INFERENCE_GW191127_050227-1126259200-400.hdf',
 'H1L1V1-INFERENCE_GW200128_022011-1126259200-400.hdf',
 'H1L1V1-INFERENCE_GW200209_085452-1126259200-400.hdf',
 'H1L1V1-INFERENCE_GW200216_220804-1126259200-400.hdf',
 'H1L1V1-INFERENCE_GW191105

In [11]:
results_files_220[0][17:32]

'GW200112_155838'

In [18]:
bayes_factors

{'GW200112_155838': -580379.0443251084,
 'GW191103_012549': -499519.0434312917,
 'GW200219_094415': -670808.1224321208,
 'GW200208_130117': -1937137.5865853848,
 'GW200209_085452': -187624.48798607942,
 'GW200128_022011': 28135.28415490483,
 'GW191127_050227': -7678464.665219367,
 'GW191105_143521': 43081.21689967869,
 'GW200216_220804': 382779.79185743735,
 'GW191222_033537': -2118996.735964193,
 'GW200308_173609': -733895.6080200705,
 'GW200202_154313': -35464.86170767635,
 'GW200224_222234': -590299.7489625921,
 'GW191215_223052': -537434.9693342786,
 'GW191126_115259': -239042.01071936777,
 'GW200316_215756': 3891458.2785921386,
 'GW200322_091133': 4480297.81559853,
 'GW200311_115853': -575996.2725190575,
 'GW200129_065458': 351212.2850675788,
 'GW191204_171526': 370514.0675706926,
 'GW191113_071753': 286753.94455809967,
 'GW191129_134029': -170925.60294033482,
 'GW200220_061928': -105223.30495985295,
 'GW200225_060421': 1118126.0724788252,
 'GW191219_163120': -4215906.520155029,
 

# Explore a particular event

In [19]:
ename = 'GW200112_155838'

In [28]:
rundir = "/work/yifan.wang/ringdown/t6-rerun4ogc-geocent_time/220_221/o3bringdown_output/"
#rundir = "/work/julian.westerweck/projects/ringdown/4ogc/workflows/220_merger/4ogc/4ogc_ringdown_test_output/"

snr = {}
configdir = glob.glob(rundir+'config_files/*'+ename+'*')
sampledir = glob.glob(rundir+'samples_files/*'+ename+'*')
cp = WorkflowConfigParser(configdir)
fp = io.loadfile(sampledir[0], 'r')
data = fp.read_data()                                                           
psds = fp.read_psds()  
samples = fp.read_samples(fp['samples'].keys())
idx = samples['loglikelihood'].argmax()
maxl_params = {p: samples[p][idx] for p in samples.fieldnames}
model = models.read_from_config(cp,data=data,psds=psds)
model.update(**maxl_params)
snr[ename] = conversions.snr_from_loglr(model.loglr)

In [29]:
snr

{'GW200112_155838': 7.6404290555216114}

In [31]:
pol = model.current_stats['maxl_polarization']
#compute the max loglikelihood waveform
wfs = model.waveform_generator.generate(polarization=pol,**model.current_params)    

In [33]:
model.data

{'L1': <pycbc.types.frequencyseries.FrequencySeries at 0x7f2f1ec14a90>,
 'V1': <pycbc.types.frequencyseries.FrequencySeries at 0x7f2f1ec151d0>}

In [35]:
model.get_waveforms()

{'L1': (<pycbc.types.frequencyseries.FrequencySeries at 0x7f2eeedde240>,
  <pycbc.types.frequencyseries.FrequencySeries at 0x7f2eeeddec50>),
 'V1': (<pycbc.types.frequencyseries.FrequencySeries at 0x7f2eeeddeef0>,
  <pycbc.types.frequencyseries.FrequencySeries at 0x7f2eeeddef60>)}

In [37]:
model.psds

{'L1': <pycbc.types.frequencyseries.FrequencySeries at 0x7f2f1f42d128>,
 'V1': <pycbc.types.frequencyseries.FrequencySeries at 0x7f2f1f42d160>}

In [45]:
model.get_gate_times()

{'L1': (1262879934.0869267, 2.000000238418579),
 'V1': (1262879934.097459, 2.0000011920928955)}

In [48]:
whdata = {}
whwaveform = {}
wf = model.get_waveforms()
for det in model.data:
    d = model.data[det]
    d = d.copy()
    d /=  (model.psds[det])**0.5
    wfd = wf[det]
    wfd = wfd.copy()
    wfd /= (model.psds[det])**0.5
    whdata[det] = d.to_timeseries()
    whwaveform[det] = wfd.to_timeseries()
    

    
    plt.figure()
    plt.plot(whdata[det].sample_times,whdata[det],label=det)
    plt.ylim(-200,200)
    plt.legend()

AttributeError: 'tuple' object has no attribute 'copy'

In [49]:
wf

{'L1': (<pycbc.types.frequencyseries.FrequencySeries at 0x7f2eeedde240>,
  <pycbc.types.frequencyseries.FrequencySeries at 0x7f2eeeddec50>),
 'V1': (<pycbc.types.frequencyseries.FrequencySeries at 0x7f2eeeddeef0>,
  <pycbc.types.frequencyseries.FrequencySeries at 0x7f2eeeddef60>)}

In [40]:
whdata['L1'].sample_timesa

In [32]:
whdata = {}
for det in model.data:
    d = model.data[det]
    d = d.copy()
    d *= model.weight[det] / (4*model.psds[det].delta_f)**0.5
    whdata[det] = d.to_timeseries()
    
    waveforms = {}
    whitened_waveforms = {}
    for detname in wfs:
        hs = {}
        whitend_hs = {}
        det = Detector(detname)
        fp, fc = det.antenna_pattern(model.current_params['ra'],
                                     model.current_params['dec'],
                                     pol,
                                     model.current_params['tc'])
        hp, hc = wfs[detname]
        h = fp*hp + fc*hc
        h.resize(len(model.weight[detname]))
        wh = h.copy()
        wh *= model.weight[detname] / (4*model.psds[detname].delta_f)**0.5
        whitened_waveforms[detname] = wh.to_timeseries() 

KeyError: 'L1'

In [1]:
def fn_to_waveform(fn):       
    # read in the raw posterior file and extract the max loglikelihood parameter value
    with io.loadfile(fn, 'r') as fp:   
        data = fp.read_data()                                                           
        psds = fp.read_psds()                                                           
        cp = fp.read_config_file()
        samples = fp.read_samples(list(fp['samples'].keys()))
        idx = samples['loglikelihood'].argmax()
        params = {p: samples[p][idx] for p in samples.fieldnames}
    # set up the model
    model = models.read_from_config(cp, data=data, psds=psds)
    model.update(**params)
    _ = model.loglikelihood
    pol = model.current_stats['maxl_polarization']
    #compute the max loglikelihood waveform
    wfs = model.waveform_generator.generate(polarization=pol,**model.current_params)
    
    whdata = {}
    for det in model.data:
        d = model.data[det]
        d = d.copy()
        d *= model.weight[det] / (4*model.psds[det].delta_f)**0.5
        whdata[det] = d.to_timeseries()
    
    waveforms = {}
    whitened_waveforms = {}
    for detname in wfs:
        hs = {}
        whitend_hs = {}
        det = Detector(detname)
        fp, fc = det.antenna_pattern(model.current_params['ra'],
                                     model.current_params['dec'],
                                     pol,
                                     model.current_params['tc'])
        hp, hc = wfs[detname]
        h = fp*hp + fc*hc
        h.resize(len(model.weight[detname]))
        wh = h.copy()
        wh *= model.weight[detname] / (4*model.psds[detname].delta_f)**0.5
        whitened_waveforms[detname] = wh.to_timeseries() 
    return whdata, whitened_waveforms,model

In [3]:
from pycbc.catalog import Catalog

In [5]:
catalog = Catalog(source='gwtc-2.1')

In [6]:
catalog.names

dict_keys(['GW190403_051519-v1', 'GW190408_181802-v2', 'GW190412_053044-v4', 'GW190413_052954-v2', 'GW190413_134308-v2', 'GW190421_213856-v2', 'GW190425_081805-v3', 'GW190426_190642-v1', 'GW190503_185404-v2', 'GW190512_180714-v2', 'GW190513_205428-v2', 'GW190514_065416-v2', 'GW190517_055101-v2', 'GW190519_153544-v2', 'GW190521_030229-v4', 'GW190521_074359-v2', 'GW190527_092055-v2', 'GW190602_175927-v2', 'GW190620_030421-v2', 'GW190630_185205-v2', 'GW190701_203306-v2', 'GW190706_222641-v2', 'GW190707_093326-v2', 'GW190708_232457-v2', 'GW190719_215514-v2', 'GW190720_000836-v2', 'GW190725_174728-v1', 'GW190727_060333-v2', 'GW190728_064510-v2', 'GW190731_140936-v2', 'GW190803_022701-v2', 'GW190805_211137-v1', 'GW190814_211039-v3', 'GW190828_063405-v2', 'GW190828_065509-v2', 'GW190910_112807-v2', 'GW190915_235702-v2', 'GW190916_200658-v1', 'GW190917_114630-v1', 'GW190924_021846-v2', 'GW190925_232845-v1', 'GW190926_050336-v1', 'GW190929_012149-v2', 'GW190930_133541-v2'])

In [8]:
catalog['GW190620_030421-v2'].data['strain']

[{'GPSstart': 1245035064,
  'detector': 'L1',
  'duration': 32,
  'format': 'gwf',
  'sampling_rate': 16384,
  'url': 'https://www.gw-openscience.org/eventapi/json/GWTC-2.1-confident/GW190620_030421/v2/L-L1_GWOSC_16KHZ_R1-1245035064-32.gwf'},
 {'GPSstart': 1245035064,
  'detector': 'L1',
  'duration': 32,
  'format': 'hdf5',
  'sampling_rate': 16384,
  'url': 'https://www.gw-openscience.org/eventapi/json/GWTC-2.1-confident/GW190620_030421/v2/L-L1_GWOSC_16KHZ_R1-1245035064-32.hdf5'},
 {'GPSstart': 1245035064,
  'detector': 'L1',
  'duration': 32,
  'format': 'txt',
  'sampling_rate': 16384,
  'url': 'https://www.gw-openscience.org/eventapi/json/GWTC-2.1-confident/GW190620_030421/v2/L-L1_GWOSC_16KHZ_R1-1245035064-32.txt.gz'},
 {'GPSstart': 1245035064,
  'detector': 'L1',
  'duration': 32,
  'format': 'gwf',
  'sampling_rate': 4096,
  'url': 'https://www.gw-openscience.org/eventapi/json/GWTC-2.1-confident/GW190620_030421/v2/L-L1_GWOSC_4KHZ_R1-1245035064-32.gwf'},
 {'GPSstart': 1245035064,